In [1]:
import pandas as pd

In [2]:
df = pd.read_csv('Toronto.csv')
print(df.shape)
df.head()

(103, 5)


Postal Code      Borough                           Neighbourhood   Latitude  \
0         M1B  Scarborough                          Rouge, Malvern  43.806686   
1         M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.784535   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3         M1G  Scarborough                                  Woburn  43.770992   
4         M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [3]:
#choose boroughs that contain word Toronto
#df = df[df['Borough'].apply(lambda x: 'Toronto' in x)]
#df.reset_index(drop=True, inplace=True)
#df

In [4]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [5]:
address = 'Toronto, Ontario'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print("Toronto's latitude and longitude are{}, {}".format(latitude, longitude))

/anaconda3/envs/UdacityDL/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.18.1" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


Toronto's latitude and longitude are43.653963, -79.387207


In [6]:
#Create a map of Toronto using the latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

#add markers to the map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False
    ).add_to(map_toronto)
    
map_toronto

In [7]:
#Foursquare API Information

CLIENT_ID = 'KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A' # your Foursquare ID
CLIENT_SECRET = 'G45VQYWWOOZ3KFDYS2FUATXVMWC1CTY4VYSUTMR0I2RXK0WU' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('My credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

My credentails:
CLIENT_ID: KDCNWHDEJ4UYTSB3QHKSYWIS1JX0WZI50JRRQT540WXZSP2A
CLIENT_SECRET:G45VQYWWOOZ3KFDYS2FUATXVMWC1CTY4VYSUTMR0I2RXK0WU


In [8]:
#function that extract the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) ==0:
        return None
    else:
        return categories_list[0]['name']

In [9]:
radius=500
LIMIT=100
def getNearbyVenues(names, latitudes, longitudes, radius=600):
    venues_list = []
    for name, lat, lng in zip(names, latitudes, longitudes):
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        venues_list.append([(
            name,
            lat,
            lng,
            v['venue']['name'],
            v['venue']['location']['lat'],
            v['venue']['location']['lng'],
            v['venue']['categories'][0]['name']) for v in results])
        
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood',
                             'Neighbourhood Latitude',
                             'Neighbourhood Longitude',
                             'Venue',
                             'Venue Latitude',
                             'Venue Longitude',
                             'Venue Category']
    
    return (nearby_venues)

In [10]:
toronto_venues = getNearbyVenues(df['Neighbourhood'], df['Latitude'], df['Longitude'])

In [11]:
toronto_venues.head()
print(toronto_venues.shape)

(2852, 7)


In [12]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                
Adelaide, King, Richmond                                               100   
Agincourt                                                                5   
Agincourt North, L'Amoreaux East, Milliken, Ste...                       4   
Albion Gardens, Beaumond Heights, Humbergate, J...                      15   
Alderwood, Long Branch                                                   9   
Bathurst Manor, Downsview North, Wilson Heights                         20   
Bayview Village                                                          4   
Bedford Park, Lawrence Manor East                                       30   
Berczy Park                                                             94   
Birch Cliff, Cliffside West                                              5   
Bloordale Gardens, Eringate, Markland Wood, Old...                       7   
Brockton, Exhibition Place, Parkdale Village                            39   
Business reply mail Processing Centre969 Eastern                        26   
CFB Toronto, Downsview East                                              6   
CN Tower, Bathurst Quay, Island airport, Harbou...                      17   
Cabbagetown, St. James Town                                             60   
Caledonia-Fairbanks                                                     10   
Canada Post Gateway Processing Centre                                   29   
Cedarbrae                                                               14   
Central Bay Street                                                     100   
Chinatown, Grange Park, Kensington Market                              100   
Christie                                                                17   
Church and Wellesley                                                   100   
Clairlea, Golden Mile, Oakridge                                         14   
Clarks Corners, Sullivan, Tam O'Shanter                                 12   
Cliffcrest, Cliffside, Scarborough Village West                          5   
Cloverdale, Islington, Martin Grove, Princess G...                       6   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              48   
Davisville North                                                        16   
Deer Park, Forest Hill SE, Rathnelly, South Hil...                      51   
Del Ray, Keelesdale, Mount Dennis, Silverthorn                           4   
Design Exchange, Toronto Dominion Centre                               100   
Don Mills North                                                          9   
Dorset Park, Scarborough Town Centre, Wexford H...                      13   
Dovercourt Village, Dufferin                                            24   
Downsview Central                                                        4   
Downsview Northwest                                                      7   
Downsview West                                                           7   
East Birchmount Park, Ionview, Kennedy Park                             11   
East Toronto                                                            16   
Emery, Humberlea                                                         2   
Fairview, Henry Farm, Oriole                                            57   
First Canadian Place, Underground city                                 100   
Flemingdon Park, Don Mills South                                        21   
Forest Hill North, Forest Hill West                                      4   
Glencairn                                                                4   
Guildwood, Morningside, West Hill                                       11   
Harbord, University of Toronto                                          73   
Harbourfront East, Toronto Islands, Union Station                      100

In [13]:
toronto_onehot = pd.get_dummies(toronto_venues['Venue Category'], prefix='', prefix_sep='')
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood']

fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Accessories Store  Adult Boutique  \
0                          Rouge, Malvern                  0               0   
1                          Rouge, Malvern                  0               0   
2                          Rouge, Malvern                  0               0   
3                          Rouge, Malvern                  0               0   
4  Highland Creek, Rouge Hill, Port Union                  0               0   

   Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0                  0        0                   0             0   
1                  0        0                   0             0   
2                  0        0                   0             0   
3                  0        0                   0             0   
4                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Amphitheater  Animal Shelter  Antique Shop  Aquarium  Arcade  \
0             0               0             0         0       0   
1             0               0             0         0       0   
2             0               0             0         0       0   
3             0               0             0         0       0   
4             0               0             0         0       0   

   Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                 0            0           0                    0   
1                 0            0           0                    0   
2                 0            0           0                    0   
3                 0            0           0                    0   
4                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Dealership  BBQ Joint  \
0                 0                   0                0          0   
1                 0                   0                0          0   
2                 0                   0                0          0   
3                 0                   0                0          0   
4                 0                   0                0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    1               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  Beer Bar  \
0                 0                 0                   0      0         0   
1                 0                 0                   0      0         0   
2                 0                 0                   0      0         0   
3                 0                 0                   0      0         0   
4                 0                 0                   0      0         0   

   Beer Store  Belgian Restaurant  Bike Rental / Bike Share  Bike Shop  \
0           0                   0                         0          0   
1           0                   0                         0          0   
2           0                   0                         0          0   
3           0                   0                         0          0   
4           0                   0                         0          0   

   Bistro  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0       0              0          0         0              0   
1       0

In [14]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_grouped

Neighbourhood  Accessories Store  \
0                             Adelaide, King, Richmond               0.00   
1                                            Agincourt               0.00   
2    Agincourt North, L'Amoreaux East, Milliken, St...               0.00   
3    Albion Gardens, Beaumond Heights, Humbergate, ...               0.00   
4                               Alderwood, Long Branch               0.00   
5      Bathurst Manor, Downsview North, Wilson Heights               0.00   
6                                      Bayview Village               0.00   
7                    Bedford Park, Lawrence Manor East               0.00   
8                                          Berczy Park               0.00   
9                          Birch Cliff, Cliffside West               0.00   
10   Bloordale Gardens, Eringate, Markland Wood, Ol...               0.00   
11        Brockton, Exhibition Place, Parkdale Village               0.00   
12    Business reply mail Processing Centre969 Eastern               0.00   
13                         CFB Toronto, Downsview East               0.00   
14   CN Tower, Bathurst Quay, Island airport, Harbo...               0.00   
15                         Cabbagetown, St. James Town               0.00   
16                                 Caledonia-Fairbanks               0.00   
17               Canada Post Gateway Processing Centre               0.00   
18                                           Cedarbrae               0.00   
19                                  Central Bay Street               0.00   
20           Chinatown, Grange Park, Kensington Market               0.00   
21                                            Christie               0.00   
22                                Church and Wellesley               0.00   
23                     Clairlea, Golden Mile, Oakridge               0.00   
24             Clarks Corners, Sullivan, Tam O'Shanter               0.00   
25     Cliffcrest, Cliffside, Scarborough Village West               0.00   
26   Cloverdale, Islington, Martin Grove, Princess ...               0.00   
27                      Commerce Court, Victoria Hotel               0.00   
28                                          Davisville               0.00   
29                                    Davisville North               0.00   
30   Deer Park, Forest Hill SE, Rathnelly, South Hi...               0.00   
31      Del Ray, Keelesdale, Mount Dennis, Silverthorn               0.00   
32            Design Exchange, Toronto Dominion Centre               0.00   
33                                     Don Mills North               0.00   
34   Dorset Park, Scarborough Town Centre, Wexford ...               0.00   
35                        Dovercourt Village, Dufferin               0.00   
36                                   Downsview Central               0.00   
37                                 Downsview Northwest               0.00   
38                                      Downsview West               0.00   
39         East Birchmount Park, Ionview, Kennedy Park               0.00   
40                                        East Toronto               0.00   
41                                    Emery, Humberlea               0.00   
42                        Fairview, Henry Farm, Oriole               0.00   
43              First Canadian Place, Underground city               0.00   
44                    Flemingdon Park, Don Mills South               0.00   
45                 Forest Hill North, Forest Hill West               0.00   
46                                           Glencairn               0.00   
47                   Guildwood, Morningside, West Hill               0.00   
48                      Harbord, University of Toronto               0.00   
49   Harbourfront East, Toronto Islands, Union Station               0.00   
50                           Harbourfront, Regent Park               0.00   
51                       High Park, T

In [15]:
#normalize each column's data

'''for i in  range(1, len(toronto_grouped.columns)-1):
    min_val = toronto_grouped.iloc[:, i].min()
    max_val = toronto_grouped.iloc[:, i].max()
    toronto_grouped.iloc[:, i] = toronto_grouped.iloc[:, i].apply(lambda x: (x-min_val) / (max_val- min_val))
toronto_grouped'''

for i in range(len(toronto_grouped)):
    mean = toronto_grouped.iloc[i, 1:].mean()
    std = toronto_grouped.iloc[i, 1:].std()
    toronto_grouped.iloc[i, 1:] = (toronto_grouped.iloc[i, 1:] - mean) / std

toronto_grouped

Neighbourhood  Accessories Store  \
0                             Adelaide, King, Richmond          -0.381693   
1                                            Agincourt          -0.130635   
2    Agincourt North, L'Amoreaux East, Milliken, St...          -0.116644   
3    Albion Gardens, Beaumond Heights, Humbergate, ...          -0.203441   
4                               Alderwood, Long Branch          -0.159180   
5      Bathurst Manor, Downsview North, Wilson Heights          -0.254933   
6                                      Bayview Village          -0.116644   
7                    Bedford Park, Lawrence Manor East          -0.265112   
8                                          Berczy Park          -0.392722   
9                          Birch Cliff, Cliffside West          -0.130635   
10   Bloordale Gardens, Eringate, Markland Wood, Ol...          -0.155102   
11        Brockton, Exhibition Place, Parkdale Village          -0.326499   
12    Business reply mail Processing Centre969 Eastern          -0.286046   
13                         CFB Toronto, Downsview East          -0.123826   
14   CN Tower, Bathurst Quay, Island airport, Harbo...          -0.200904   
15                         Cabbagetown, St. James Town          -0.304980   
16                                 Caledonia-Fairbanks          -0.169621   
17               Canada Post Gateway Processing Centre          -0.216573   
18                                           Cedarbrae          -0.194757   
19                                  Central Bay Street          -0.319694   
20           Chinatown, Grange Park, Kensington Market          -0.363237   
21                                            Christie          -0.179714   
22                                Church and Wellesley          -0.376817   
23                     Clairlea, Golden Mile, Oakridge          -0.175558   
24             Clarks Corners, Sullivan, Tam O'Shanter          -0.176479   
25     Cliffcrest, Cliffside, Scarborough Village West          -0.130635   
26   Cloverdale, Islington, Martin Grove, Princess ...          -0.123826   
27                      Commerce Court, Victoria Hotel          -0.330975   
28                                          Davisville          -0.292702   
29                                    Davisville North          -0.238218   
30   Deer Park, Forest Hill SE, Rathnelly, South Hi...          -0.295076   
31      Del Ray, Keelesdale, Mount Dennis, Silverthorn          -0.116644   
32            Design Exchange, Toronto Dominion Centre          -0.288801   
33                                     Don Mills North          -0.159180   
34   Dorset Park, Scarborough Town Centre, Wexford ...          -0.185781   
35                        Dovercourt Village, Dufferin          -0.253572   
36                                   Downsview Central          -0.116644   
37                                 Downsview Northwest          -0.155102   
38                                      Downsview West          -0.155102   
39         East Birchmount Park, Ionview, Kennedy Park          -0.166808   
40                                        East Toronto          -0.201594   
41                                    Emery, Humberlea          -0.082200   
42                        Fairview, Henry Farm, Oriole          -0.311916   
43              First Canadian Place, Underground city          -0.325701   
44                    Flemingdon Park, Don Mills South          -0.223917   
45                 Forest Hill North, Forest Hill West          -0.116644   
46                                           Glencairn          -0.116644   
47                   Guildwood, Morningside, West Hill          -0.179566   
48                      Harbord, University of Toronto          -0.363876   
49   Harbourfront East, Toronto Islands, Union Station          -0.321659   
50                           Harbourfront, Regent Park          -0.279553   
51                       High Park, T

In [16]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [17]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))
        
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood' ] = toronto_grouped['Neighbourhood']

for ind  in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)
    
neighborhoods_venues_sorted
    
    

Neighbourhood  \
0                             Adelaide, King, Richmond   
1                                            Agincourt   
2    Agincourt North, L'Amoreaux East, Milliken, St...   
3    Albion Gardens, Beaumond Heights, Humbergate, ...   
4                               Alderwood, Long Branch   
5      Bathurst Manor, Downsview North, Wilson Heights   
6                                      Bayview Village   
7                    Bedford Park, Lawrence Manor East   
8                                          Berczy Park   
9                          Birch Cliff, Cliffside West   
10   Bloordale Gardens, Eringate, Markland Wood, Ol...   
11        Brockton, Exhibition Place, Parkdale Village   
12    Business reply mail Processing Centre969 Eastern   
13                         CFB Toronto, Downsview East   
14   CN Tower, Bathurst Quay, Island airport, Harbo...   
15                         Cabbagetown, St. James Town   
16                                 Caledonia-Fairbanks   
17               Canada Post Gateway Processing Centre   
18                                           Cedarbrae   
19                                  Central Bay Street   
20           Chinatown, Grange Park, Kensington Market   
21                                            Christie   
22                                Church and Wellesley   
23                     Clairlea, Golden Mile, Oakridge   
24             Clarks Corners, Sullivan, Tam O'Shanter   
25     Cliffcrest, Cliffside, Scarborough Village West   
26   Cloverdale, Islington, Martin Grove, Princess ...   
27                      Commerce Court, Victoria Hotel   
28                                          Davisville   
29                                    Davisville North   
30   Deer Park, Forest Hill SE, Rathnelly, South Hi...   
31      Del Ray, Keelesdale, Mount Dennis, Silverthorn   
32            Design Exchange, Toronto Dominion Centre   
33                                     Don Mills North   
34   Dorset Park, Scarborough Town Centre, Wexford ...   
35                        Dovercourt Village, Dufferin   
36                                   Downsview Central   
37                                 Downsview Northwest   
38                                      Downsview West   
39         East Birchmount Park, Ionview, Kennedy Park   
40                                        East Toronto   
41                                    Emery, Humberlea   
42                        Fairview, Henry Farm, Oriole   
43              First Canadian Place, Underground city   
44                    Flemingdon Park, Don Mills South   
45                 Forest Hill North, Forest Hill West   
46                                           Glencairn   
47                   Guildwood, Morningside, West Hill   
48                      Harbord, University of Toronto   
49   Harbourfront East, Toronto Islands, Union Station   
50                           Harbourfront, Regent Park   
51                       High Park, The Junction South   
52              Highland Creek, Rouge Hill, Port Union   
53                                   Hillcrest Village   
54        Humber Bay Shores, Mimico South, New Toronto   
55   Humber Bay, King's Mill Park, Kingsway Park So...   
56                                       Humber Summit   
57                                  Humewood-Cedarvale   
58                                    Islington Avenue   
59   Kingsview Village, Martin Grove Gardens, Richv...   
60   Kingsway Park South West, Mimico NW, The Queen...   
61                       L'Amoreaux West, Steeles West   
62                    Lawrence Heights, Lawrence Manor   
63                                       Lawrence Park   
64                                             Leaside   
65                            Little Portugal, Trinity   
66            Maple Leaf Park, North Park, Upwood Park   
67                                   Maryvale, Wexford   
68                         Moore Park, 

In [64]:
kclusters = 3

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', axis=1)

kmeans = KMeans(kclusters, random_state=0).fit(toronto_grouped_clustering)

kmeans.labels_[:10]

array([2, 1, 0, 1, 1, 2, 1, 2, 2, 1], dtype=int32)

In [65]:
print(df.shape)

print(kmeans.labels_.shape)

(103, 5)
(101,)


In [66]:
#add cluster labels to the columns
neighborhoods_venues_sorted['Cluster Labels'] = kmeans.labels_
neighborhoods_venues_sorted

Neighbourhood  \
0                             Adelaide, King, Richmond   
1                                            Agincourt   
2    Agincourt North, L'Amoreaux East, Milliken, St...   
3    Albion Gardens, Beaumond Heights, Humbergate, ...   
4                               Alderwood, Long Branch   
5      Bathurst Manor, Downsview North, Wilson Heights   
6                                      Bayview Village   
7                    Bedford Park, Lawrence Manor East   
8                                          Berczy Park   
9                          Birch Cliff, Cliffside West   
10   Bloordale Gardens, Eringate, Markland Wood, Ol...   
11        Brockton, Exhibition Place, Parkdale Village   
12    Business reply mail Processing Centre969 Eastern   
13                         CFB Toronto, Downsview East   
14   CN Tower, Bathurst Quay, Island airport, Harbo...   
15                         Cabbagetown, St. James Town   
16                                 Caledonia-Fairbanks   
17               Canada Post Gateway Processing Centre   
18                                           Cedarbrae   
19                                  Central Bay Street   
20           Chinatown, Grange Park, Kensington Market   
21                                            Christie   
22                                Church and Wellesley   
23                     Clairlea, Golden Mile, Oakridge   
24             Clarks Corners, Sullivan, Tam O'Shanter   
25     Cliffcrest, Cliffside, Scarborough Village West   
26   Cloverdale, Islington, Martin Grove, Princess ...   
27                      Commerce Court, Victoria Hotel   
28                                          Davisville   
29                                    Davisville North   
30   Deer Park, Forest Hill SE, Rathnelly, South Hi...   
31      Del Ray, Keelesdale, Mount Dennis, Silverthorn   
32            Design Exchange, Toronto Dominion Centre   
33                                     Don Mills North   
34   Dorset Park, Scarborough Town Centre, Wexford ...   
35                        Dovercourt Village, Dufferin   
36                                   Downsview Central   
37                                 Downsview Northwest   
38                                      Downsview West   
39         East Birchmount Park, Ionview, Kennedy Park   
40                                        East Toronto   
41                                    Emery, Humberlea   
42                        Fairview, Henry Farm, Oriole   
43              First Canadian Place, Underground city   
44                    Flemingdon Park, Don Mills South   
45                 Forest Hill North, Forest Hill West   
46                                           Glencairn   
47                   Guildwood, Morningside, West Hill   
48                      Harbord, University of Toronto   
49   Harbourfront East, Toronto Islands, Union Station   
50                           Harbourfront, Regent Park   
51                       High Park, The Junction South   
52              Highland Creek, Rouge Hill, Port Union   
53                                   Hillcrest Village   
54        Humber Bay Shores, Mimico South, New Toronto   
55   Humber Bay, King's Mill Park, Kingsway Park So...   
56                                       Humber Summit   
57                                  Humewood-Cedarvale   
58                                    Islington Avenue   
59   Kingsview Village, Martin Grove Gardens, Richv...   
60   Kingsway Park South West, Mimico NW, The Queen...   
61                       L'Amoreaux West, Steeles West   
62                    Lawrence Heights, Lawrence Manor   
63                                       Lawrence Park   
64                                             Leaside   
65                            Little Portugal, Trinity   
66            Maple Leaf Park, North Park, Upwood Park   
67                                   Maryvale, Wexford   
68                         Moore Park, 

In [67]:
#merge basic data with sorted data frame
toronto_merged = df
toronto_merged = toronto_merged.merge(neighborhoods_venues_sorted, on='Neighbourhood', how='left')
toronto_merged

Postal Code           Borough  \
0           M1B       Scarborough   
1           M1C       Scarborough   
2           M1E       Scarborough   
3           M1G       Scarborough   
4           M1H       Scarborough   
5           M1J       Scarborough   
6           M1K       Scarborough   
7           M1L       Scarborough   
8           M1M       Scarborough   
9           M1N       Scarborough   
10          M1P       Scarborough   
11          M1R       Scarborough   
12          M1S       Scarborough   
13          M1T       Scarborough   
14          M1V       Scarborough   
15          M1W       Scarborough   
16          M1X       Scarborough   
17          M2H        North York   
18          M2J        North York   
19          M2K        North York   
20          M2L        North York   
21          M2M        North York   
22          M2N        North York   
23          M2P        North York   
24          M2R        North York   
25          M3A        North York   
26          M3B        North York   
27          M3C        North York   
28          M3H        North York   
29          M3J        North York   
30          M3K        North York   
31          M3L        North York   
32          M3M        North York   
33          M3N        North York   
34          M4A        North York   
35          M4B         East York   
36          M4C         East York   
37          M4E      East Toronto   
38          M4G         East York   
39          M4H         East York   
40          M4J         East York   
41          M4K      East Toronto   
42          M4L      East Toronto   
43          M4M      East Toronto   
44          M4N   Central Toronto   
45          M4P   Central Toronto   
46          M4R   Central Toronto   
47          M4S   Central Toronto   
48          M4T   Central Toronto   
49          M4V   Central Toronto   
50          M4W  Downtown Toronto   
51          M4X  Downtown Toronto   
52          M4Y  Downtown Toronto   
53          M5A  Downtown Toronto   
54          M5B  Downtown Toronto   
55          M5C  Downtown Toronto   
56          M5E  Downtown Toronto   
57          M5G  Downtown Toronto   
58          M5H  Downtown Toronto   
59          M5J  Downtown Toronto   
60          M5K  Downtown Toronto   
61          M5L  Downtown Toronto   
62          M5M        North York   
63          M5N   Central Toronto   
64          M5P   Central Toronto   
65          M5R   Central Toronto   
66          M5S  Downtown Toronto   
67          M5T  Downtown Toronto   
68          M5V  Downtown Toronto   
69          M5W  Downtown Toronto   
70          M5X  Downtown Toronto   
71          M6A        North York   
72          M6B        North York   
73          M6C              York   
74          M6E              York   
75          M6G  Downtown Toronto   
76          M6H      West Toronto   
77          M6J      West Toronto   
78          M6K      West Toronto   
79          M6L        North York   
80          M6M              York   
81          M6N              York   
82          M6P      West Toronto   
83          M6R      West Toronto   
84          M6S      West Toronto   
85          M7A      Queen's Park   
86          M7R       Mississauga   
87          M7Y      East Toronto   
88          M8V         Etobicoke   
89          M8W         Etobicoke   
90          M8X         Etobicoke   
91          M8Y         Etobicoke   
92          M8Z         Etobicoke   
93          M9A         Etobicoke   
94          M9B         Etobicoke   
95          M9C         Etobicoke   
96          M9L        North York   
97          M9M        North York   
98          M9N              York   
99          M9P         Etobicoke   
100         M9R         Etobicoke   
101         M9V         Etobicoke   
102         M9W         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
0                                       Rouge, Malvern  43.806686 -79.19435

In [68]:
#NaN
for i in range(len(toronto_merged)):
    if np.isnan(toronto_merged.iloc[i, -1]):
        toronto_merged.iloc[i, -1] = kclusters

In [69]:
toronto_merged['Cluster Labels'].astype(np.int64, inplace=True)

0      1
1      1
2      1
3      2
4      1
5      1
6      1
7      2
8      1
9      1
10     1
11     1
12     1
13     1
14     0
15     1
16     3
17     1
18     2
19     1
20     1
21     3
22     2
23     0
24     1
25     0
26     1
27     2
28     2
29     1
30     0
31     0
32     1
33     1
34     2
35     1
36     0
37     2
38     2
39     1
40     2
41     2
42     1
43     2
44     0
45     1
46     2
47     2
48     0
49     2
50     0
51     2
52     2
53     2
54     2
55     2
56     2
57     2
58     2
59     2
60     2
61     2
62     2
63     1
64     0
65     2
66     2
67     2
68     1
69     2
70     2
71     1
72     1
73     1
74     0
75     2
76     0
77     2
78     2
79     0
80     0
81     1
82     2
83     2
84     2
85     2
86     2
87     1
88     2
89     1
90     2
91     1
92     1
93     1
94     1
95     1
96     1
97     1
98     0
99     1
100    1
101    1
102    1
Name: Cluster Labels, dtype: int64

In [70]:
toronto_merged

Postal Code           Borough  \
0           M1B       Scarborough   
1           M1C       Scarborough   
2           M1E       Scarborough   
3           M1G       Scarborough   
4           M1H       Scarborough   
5           M1J       Scarborough   
6           M1K       Scarborough   
7           M1L       Scarborough   
8           M1M       Scarborough   
9           M1N       Scarborough   
10          M1P       Scarborough   
11          M1R       Scarborough   
12          M1S       Scarborough   
13          M1T       Scarborough   
14          M1V       Scarborough   
15          M1W       Scarborough   
16          M1X       Scarborough   
17          M2H        North York   
18          M2J        North York   
19          M2K        North York   
20          M2L        North York   
21          M2M        North York   
22          M2N        North York   
23          M2P        North York   
24          M2R        North York   
25          M3A        North York   
26          M3B        North York   
27          M3C        North York   
28          M3H        North York   
29          M3J        North York   
30          M3K        North York   
31          M3L        North York   
32          M3M        North York   
33          M3N        North York   
34          M4A        North York   
35          M4B         East York   
36          M4C         East York   
37          M4E      East Toronto   
38          M4G         East York   
39          M4H         East York   
40          M4J         East York   
41          M4K      East Toronto   
42          M4L      East Toronto   
43          M4M      East Toronto   
44          M4N   Central Toronto   
45          M4P   Central Toronto   
46          M4R   Central Toronto   
47          M4S   Central Toronto   
48          M4T   Central Toronto   
49          M4V   Central Toronto   
50          M4W  Downtown Toronto   
51          M4X  Downtown Toronto   
52          M4Y  Downtown Toronto   
53          M5A  Downtown Toronto   
54          M5B  Downtown Toronto   
55          M5C  Downtown Toronto   
56          M5E  Downtown Toronto   
57          M5G  Downtown Toronto   
58          M5H  Downtown Toronto   
59          M5J  Downtown Toronto   
60          M5K  Downtown Toronto   
61          M5L  Downtown Toronto   
62          M5M        North York   
63          M5N   Central Toronto   
64          M5P   Central Toronto   
65          M5R   Central Toronto   
66          M5S  Downtown Toronto   
67          M5T  Downtown Toronto   
68          M5V  Downtown Toronto   
69          M5W  Downtown Toronto   
70          M5X  Downtown Toronto   
71          M6A        North York   
72          M6B        North York   
73          M6C              York   
74          M6E              York   
75          M6G  Downtown Toronto   
76          M6H      West Toronto   
77          M6J      West Toronto   
78          M6K      West Toronto   
79          M6L        North York   
80          M6M              York   
81          M6N              York   
82          M6P      West Toronto   
83          M6R      West Toronto   
84          M6S      West Toronto   
85          M7A      Queen's Park   
86          M7R       Mississauga   
87          M7Y      East Toronto   
88          M8V         Etobicoke   
89          M8W         Etobicoke   
90          M8X         Etobicoke   
91          M8Y         Etobicoke   
92          M8Z         Etobicoke   
93          M9A         Etobicoke   
94          M9B         Etobicoke   
95          M9C         Etobicoke   
96          M9L        North York   
97          M9M        North York   
98          M9N              York   
99          M9P         Etobicoke   
100         M9R         Etobicoke   
101         M9V         Etobicoke   
102         M9W         Etobicoke   

                                         Neighbourhood   Latitude  Longitude  \
0                                       Rouge, Malvern  43.806686 -79.19435

In [71]:
#create a map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)

#set color scheme for the clusters
x = np.arange(kclusters+1)
ys = [i+x+(i*x)**2 for i in range(kclusters+1)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' +str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
    
map_clusters

Cluster1

In [72]:
toronto_merged.loc[toronto_merged['Cluster Labels']==0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough       1st Most Common Venue  2nd Most Common Venue  \
14       Scarborough        Fast Food Restaurant                   Park   
23        North York                        Park                   Bank   
25        North York                    Bus Stop              Pet Store   
30        North York                        Park             Food Court   
31        North York               Shopping Mall  Vietnamese Restaurant   
36         East York                        Park           Skating Rink   
44   Central Toronto          Dim Sum Restaurant               Bus Line   
48   Central Toronto                        Park                    Gym   
50  Downtown Toronto                        Park                  Trail   
64   Central Toronto                       Trail                   Park   
74              York                        Park                    Gym   
76      West Toronto                    Pharmacy                 Bakery   
79        North York  Construction & Landscaping                   Park   
80              York           Convenience Store         Sandwich Place   
98              York                 Snack Place                   Park   

   3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
14            Playground              BBQ Joint           Yoga Studio   
23           Yoga Studio              Drugstore                 Diner   
25  Fast Food Restaurant                   Park     Food & Drink Shop   
30              Bus Stop                Airport     Electronics Store   
31                  Bank            Pizza Place         Moving Target   
36              Pharmacy         Cosmetics Shop                   Spa   
44                  Park            Swim School            Donut Shop   
48            Playground            Yoga Studio      Doner Restaurant   
50            Playground            Yoga Studio          Dessert Shop   
64         Jewelry Store       Sushi Restaurant           Yoga Studio   
74  Fast Food Restaurant                 Bakery    Mexican Restaurant   
76           Supermarket                   Park          Liquor Store   
79                Bakery           Home Service             Drugstore   
80                  Park  Check Cashing Service      Doner Restaurant   
98           Yoga Studio       Doner Restaurant          Dessert Shop   

    Cluster Labels  
14             0.0  
23             0.0  
25             0.0  
30             0.0  
31             0.0  
36             0.0  
44             0.0  
48             0.0  
50             0.0  
64             0.0  
74             0.0  
76             0.0  
79             0.0  
80             0.0  
98             0.0

In [73]:
toronto_merged.loc[toronto_merged['Cluster Labels']==1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough   1st Most Common Venue      2nd Most Common Venue  \
0         Scarborough    Fast Food Restaurant                        Spa   
1         Scarborough          History Museum                        Bar   
2         Scarborough             Pizza Place             Medical Center   
4         Scarborough                  Bakery          Indian Restaurant   
5         Scarborough              Playground  Middle Eastern Restaurant   
6         Scarborough       Convenience Store             Discount Store   
8         Scarborough             Wings Joint                      Motel   
9         Scarborough                    Café            College Stadium   
10        Scarborough       Electronics Store          Indian Restaurant   
11        Scarborough           Grocery Store               Intersection   
12        Scarborough  Furniture / Home Store                     Lounge   
13        Scarborough                Pharmacy                Pizza Place   
15        Scarborough      Chinese Restaurant       Fast Food Restaurant   
17         North York    Fast Food Restaurant               Tennis Court   
19         North York                    Café         Chinese Restaurant   
20         North York               Cafeteria           Department Store   
24         North York                Pharmacy              Grocery Store   
26         North York     Japanese Restaurant           Basketball Court   
29         North York          Massage Studio              Metro Station   
32         North York        Business Service             Baseball Field   
33         North York    Gym / Fitness Center       Fast Food Restaurant   
35          East York             Pizza Place       Fast Food Restaurant   
39          East York       Indian Restaurant          Afghan Restaurant   
42       East Toronto          Sandwich Place                        Gym   
45    Central Toronto                     Gym                      Hotel   
63    Central Toronto                     Spa                     Garden   
68   Downtown Toronto        Airport Terminal              Boat or Ferry   
71         North York  Furniture / Home Store             Clothing Store   
72         North York     Japanese Restaurant              Grocery Store   
73               York                     Spa                      Field   
81               York             Pizza Place     Furniture / Home Store   
87       East Toronto      Light Rail Station              Burrito Place   
89          Etobicoke             Pizza Place                   Pharmacy   
91          Etobicoke          Baseball Field             Breakfast Spot   
92          Etobicoke                     Gym     Thrift / Vintage Store   
93          Etobicoke                Pharmacy              Grocery Store   
94          Etobicoke             Pizza Place                   Tea Room   
95          Etobicoke                    Café          Convenience Store   
96         North York               Gift Shop                Pizza Place   
97         North York       Convenience Store             Baseball Field   
99          Etobicoke             Pizza Place                Coffee Shop   
100         Etobicoke      Chinese Restaurant                   Pharmacy   
101         Etobicoke           Grocery Store                Pizza Place   
102         Etobicoke     Rental Car Location                  Drugstore   

      3rd Most Common Venue      4th Most Common Venue  5th Most Common Venue  \
0                Hobby Shop                 Donut Shop     Dim Sum Restaurant   
1               Yoga Studio                  Drugstore                  Diner   
2            Breakfast Spot        Rental Car Location               Bus Line   
4          Asian Restaurant                Flower Shop     Athletics & Sports   
5               Pizza Place       Caribbean Restaurant      Convenience Store   
6        Chinese Restaurant           Department Store            Coffee Shop   
8        Chinese Restauran

In [74]:
toronto_merged.loc[toronto_merged['Cluster Labels']==2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough 1st Most Common Venue 2nd Most Common Venue  \
3        Scarborough           Coffee Shop              Pharmacy   
7        Scarborough              Bus Line           Coffee Shop   
18        North York  Fast Food Restaurant        Clothing Store   
22        North York           Coffee Shop      Ramen Restaurant   
27        North York           Coffee Shop      Asian Restaurant   
28        North York           Coffee Shop      Community Center   
34        North York          Intersection           Coffee Shop   
37      East Toronto                   Pub             Gastropub   
38         East York           Coffee Shop   Sporting Goods Shop   
40         East York                  Café           Pizza Place   
41      East Toronto      Greek Restaurant           Coffee Shop   
43      East Toronto                  Café                   Bar   
46   Central Toronto   Sporting Goods Shop        Clothing Store   
47   Central Toronto           Pizza Place        Sandwich Place   
49   Central Toronto           Coffee Shop    Italian Restaurant   
51  Downtown Toronto            Restaurant           Coffee Shop   
52  Downtown Toronto           Coffee Shop   Japanese Restaurant   
53  Downtown Toronto           Coffee Shop                  Café   
54  Downtown Toronto           Coffee Shop        Clothing Store   
55  Downtown Toronto           Coffee Shop                 Hotel   
56  Downtown Toronto            Restaurant           Coffee Shop   
57  Downtown Toronto           Coffee Shop                  Café   
58  Downtown Toronto                  Café           Coffee Shop   
59  Downtown Toronto           Coffee Shop                 Hotel   
60  Downtown Toronto           Coffee Shop                 Hotel   
61  Downtown Toronto           Coffee Shop                  Café   
62        North York    Italian Restaurant           Coffee Shop   
65   Central Toronto        Sandwich Place                  Café   
66  Downtown Toronto                  Café           Coffee Shop   
67  Downtown Toronto                  Café                   Bar   
69  Downtown Toronto           Coffee Shop            Restaurant   
70  Downtown Toronto                  Café           Coffee Shop   
75  Downtown Toronto         Grocery Store                  Café   
77      West Toronto                   Bar            Restaurant   
78      West Toronto           Coffee Shop                   Bar   
82      West Toronto                  Café    Italian Restaurant   
83      West Toronto        Breakfast Spot             Bookstore   
84      West Toronto                  Café           Coffee Shop   
85      Queen's Park           Coffee Shop        Sandwich Place   
86       Mississauga    Chinese Restaurant           Coffee Shop   
88         Etobicoke                   Gym   Fried Chicken Joint   
90         Etobicoke                 River           Coffee Shop   

            3rd Most Common Venue  4th Most Common Venue  \
3               Korean Restaurant       Business Service   
7                          Bakery                  Diner   
18                    Coffee Shop             Restaurant   
22                     Restaurant      Korean Restaurant   
27                            Gym          Grocery Store   
28                    Pizza Place                   Bank   
34                   Hockey Arena  Portuguese Restaurant   
37           Other Great Outdoors           Neighborhood   
38                        Brewery          Grocery Store   
40              Convenience Store               Beer Bar   
41                            Pub         Ice Cream Shop   
43                    Coffee Shop                  Diner   
46                    Coffee Shop                    Spa   
47                   Dessert Shop                   Café   
49               Sushi Restaurant                    Pub   
51                    Pizza Place                   Café   
52               Sushi Restaurant           Burger Joint   
53      

In [75]:
toronto_merged.loc[toronto_merged['Cluster Labels']==3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough 1st Most Common Venue 2nd Most Common Venue  \
16  Scarborough                   NaN                   NaN   
21   North York                   NaN                   NaN   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
16                   NaN                   NaN                   NaN   
21                   NaN                   NaN                   NaN   

    Cluster Labels  
16             3.0  
21             3.0

In [76]:
#toronto_merged.loc[toronto_merged['Cluster Labels']==4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]